In [150]:
import numpy as np
import pandas as pd

from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import roc_auc_score
from sklearn.metrics import make_scorer

from sklearn.model_selection import StratifiedKFold, cross_val_score, RandomizedSearchCV
from sklearn.model_selection import train_test_split
from sklearn.ensemble import BaggingClassifier

from sklearn.ensemble import RandomForestClassifier

%matplotlib inline 

In [3]:
import pandas_profiling as pp

In [187]:
train = pd.read_csv("train.csv", sep = '\t', index_col = 0)
test = pd.read_csv("test.csv", sep = '\t', index_col = 0)

In [188]:
train.shape

(30500, 346)

In [189]:
test.head()

0  1  2  3  4  5  6         7  8  9 ...        336  337  338  339  340  \
0 NaN  1  0  0  1  0  0  0.136364  0  0 ...   0.192984    0    1    0    0   
1 NaN  1  0  0  1  0  0  0.181818  0  0 ...   0.195690    0    1    0    0   
2 NaN  1  0  0  0  0  0  0.090909  0  0 ...   0.192984    0    1    0    0   
3 NaN  1  0  0  1  0  0  0.090909  0  0 ...   0.195690    0    1    0    0   
4 NaN  1  0  0  1  0  0  0.090909  0  0 ...   0.289893    0    0    1    0   

        341  342  343  344  345  
0  0.222222    1    1    1    1  
1  0.000000    1    1    1    0  
2  0.222222    1    1    1    0  
3  0.000000    1    1    1    0  
4  0.000000    1    1    1    1  

[5 rows x 346 columns]

In [9]:
pp.ProfileReport(train)

In [10]:
pp.ProfileReport(test)

In [190]:
#Let's find columns that constant on test dataset
useless_columns = []
for column in test:
    if(test[column].unique().size == 1 and column != '0'):
        useless_columns.append((column, test[column].unique()[0]))
#useless_columns

In [191]:
#Let's drop columns that have strong correlation with others and almost 0 correlateon with target
dropped_train = train.drop(['9', '17', '117', '119', '122', '148', 
                        '152', '160', '179', '180', '78', '79', '80', '81'], axis = 1)
dropped_test = test.drop(['9', '17', '117', '119', '122', '148', 
                        '152', '160', '179', '180', '78', '79', '80', '81'], axis = 1)

#Dropping rows in which we have values that we don't have on test and then dropping constant columns
for column in useless_columns:
    dropped_train = dropped_train[dropped_train[column[0]] == column[1]]
    dropped_train = dropped_train.drop([column[0]], axis = 1)
    dropped_test = dropped_test[dropped_test[column[0]] == column[1]]
    dropped_test = dropped_test.drop([column[0]], axis = 1)

#Validation strategy
skf = StratifiedKFold(n_splits = 5, shuffle = True)

In [192]:
dropped_train.shape

(30377, 312)

In [193]:
dropped_test.shape

(4166, 312)

In [11]:
LR = LogisticRegression(class_weight = 'balanced', solver = 'sag')
params = {
    'C':(0.028, 0.05, 0.08)
    
}
gs = GridSearchCV(estimator = LR,
                  param_grid = params, 
                  scoring = 'roc_auc',
                  cv = skf,
                  n_jobs = -1,
                  verbose = 1
                 )

In [12]:
gs.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])

Fitting 5 folds for each of 3 candidates, totalling 15 fits


[Parallel(n_jobs=-1)]: Done  15 out of  15 | elapsed:   24.3s finished


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=None, shuffle=True),
       error_score='raise',
       estimator=LogisticRegression(C=1.0, class_weight='balanced', dual=False,
          fit_intercept=True, intercept_scaling=1, max_iter=100,
          multi_class='ovr', n_jobs=1, penalty='l2', random_state=None,
          solver='sag', tol=0.0001, verbose=0, warm_start=False),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'C': (0.028, 0.05, 0.08)}, pre_dispatch='2*n_jobs',
       refit=True, return_train_score='warn', scoring='roc_auc', verbose=1)

In [13]:
gs.best_params_

{'C': 0.05}

In [14]:
gs.best_score_

0.727354465502192

In [50]:
best_LogReg = gs.best_estimator_
best_LogReg.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])

LogisticRegression(C=0.05, class_weight='balanced', dual=False,
          fit_intercept=True, intercept_scaling=1, max_iter=100,
          multi_class='ovr', n_jobs=1, penalty='l2', random_state=None,
          solver='sag', tol=0.0001, verbose=0, warm_start=False)

In [51]:
dropped_test['0'] = best_LogReg.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]
dropped_test['0'].to_csv('submission.csv',header = True, index_label = True)
dropped_test.head()

0  1  2  3  4  6         7  8  10  12 ...        336  337  338  339  \
0  0.308731  1  0  0  1  0  0.136364  0   1   1 ...   0.192984    0    1    0   
1  0.781811  1  0  0  1  0  0.181818  0   1   1 ...   0.195690    0    1    0   
2  0.540696  1  0  0  0  0  0.090909  0   1   1 ...   0.192984    0    1    0   
3  0.693469  1  0  0  1  0  0.090909  0   1   1 ...   0.195690    0    1    0   
4  0.782103  1  0  0  1  0  0.090909  0   1   1 ...   0.289893    0    0    1   

   340       341  342  343  344  345  
0    0  0.222222    1    1    1    1  
1    0  0.000000    1    1    1    0  
2    0  0.222222    1    1    1    0  
3    0  0.000000    1    1    1    0  
4    0  0.000000    1    1    1    1  

[5 rows x 312 columns]

In [40]:
lg = LogisticRegression(class_weight = 'balanced')
parameters = {'max_features': [0.9, 1.], 'max_samples': [0.4, 0.5, 0.8], "base_estimator__C": [0.05, 0.06]}
bg = BaggingClassifier(lg, random_state = 42, n_estimators = 40, warm_start = True)
gsBC = GridSearchCV(estimator = bg, 
                    param_grid = parameters, 
                    scoring = 'roc_auc', 
                    cv = skf, verbose = 2, n_jobs = -1)
gsBC = gsBC.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])
print(gsBC.best_score_)

Fitting 5 folds for each of 12 candidates, totalling 60 fits
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......
[CV]  base_estimator__C=0.05, max_features=0.9, max_samples=0.4, total=  48.2s
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......
[CV]  base_estimator__C=0.05, max_features=0.9, max_samples=0.4, total=  48.7s
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.5 .......
[CV]  base_estimator__C=0.05, max_features=0.9, max_samples=0.4, total=  49.5s
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.5 .......
[CV]  base_estimator__C=0.05, max_features=0.9, max_samples=0.4, total=  50.3s
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.5 .......
[CV]  base_estimator__C=0.05, max_features=0.9, max_sam

[Parallel(n_jobs=-1)]: Done  33 tasks      | elapsed:  8.9min


[CV]  base_estimator__C=0.06, max_features=0.9, max_samples=0.4, total=  49.8s
[CV] base_estimator__C=0.06, max_features=0.9, max_samples=0.5 .......
[CV]  base_estimator__C=0.06, max_features=0.9, max_samples=0.4, total=  51.2s
[CV] base_estimator__C=0.06, max_features=0.9, max_samples=0.5 .......
[CV]  base_estimator__C=0.06, max_features=0.9, max_samples=0.5, total=  54.0s
[CV] base_estimator__C=0.06, max_features=0.9, max_samples=0.5 .......
[CV]  base_estimator__C=0.06, max_features=0.9, max_samples=0.5, total=  53.0s
[CV] base_estimator__C=0.06, max_features=0.9, max_samples=0.8 .......
[CV]  base_estimator__C=0.06, max_features=0.9, max_samples=0.5, total=  53.4s
[CV] base_estimator__C=0.06, max_features=0.9, max_samples=0.8 .......
[CV]  base_estimator__C=0.06, max_features=0.9, max_samples=0.5, total=  51.6s
[CV] base_estimator__C=0.06, max_features=0.9, max_samples=0.8 .......
[CV]  base_estimator__C=0.06, max_features=0.9, max_samples=0.5, total=  56.0s
[CV] base_estimator__

[Parallel(n_jobs=-1)]: Done  60 out of  60 | elapsed: 15.6min finished


0.728022353641213


In [42]:
gsBC.best_params_

{'base_estimator__C': 0.06, 'max_features': 1.0, 'max_samples': 0.8}

In [53]:
best_LogRegBagging = gsBC.best_estimator_
best_LogRegBagging.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])

/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/bagging.py:348: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  warn("Warm-start fitting without increasing n_estimators does not "


BaggingClassifier(base_estimator=LogisticRegression(C=0.06, class_weight='balanced', dual=False,
          fit_intercept=True, intercept_scaling=1, max_iter=100,
          multi_class='ovr', n_jobs=1, penalty='l2', random_state=None,
          solver='liblinear', tol=0.0001, verbose=0, warm_start=False),
         bootstrap=True, bootstrap_features=False, max_features=1.0,
         max_samples=0.8, n_estimators=40, n_jobs=1, oob_score=False,
         random_state=42, verbose=0, warm_start=True)

In [60]:
dropped_test['0'] = best_LogRegBagging.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]
dropped_test['0'].to_csv('submissionBagging.csv',header = True, index_label = True)
dropped_test.head()

0  1  2  3  4  6         7  8  10  12 ...        336  337  338  339  \
0  0.310863  1  0  0  1  0  0.136364  0   1   1 ...   0.192984    0    1    0   
1  0.783763  1  0  0  1  0  0.181818  0   1   1 ...   0.195690    0    1    0   
2  0.536173  1  0  0  0  0  0.090909  0   1   1 ...   0.192984    0    1    0   
3  0.699760  1  0  0  1  0  0.090909  0   1   1 ...   0.195690    0    1    0   
4  0.777766  1  0  0  1  0  0.090909  0   1   1 ...   0.289893    0    0    1   

   340       341  342  343  344  345  
0    0  0.222222    1    1    1    1  
1    0  0.000000    1    1    1    0  
2    0  0.222222    1    1    1    0  
3    0  0.000000    1    1    1    0  
4    0  0.000000    1    1    1    1  

[5 rows x 312 columns]

In [31]:
rf = RandomForestClassifier(n_estimators = 500,
                            n_jobs = -1, 
                            verbose = 1, 
                            class_weight = 'balanced',
                            warm_start = True
                           )

params = {
    'max_depth': (7, 8),
    'min_samples_leaf': (2, 5),
}
gsRF = GridSearchCV(estimator = rf,
                  param_grid = params, 
                  scoring = 'roc_auc',
                  cv = skf,
                  n_jobs = -1,
                  verbose = 1
                 )
gsRF.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])

Fitting 5 folds for each of 4 candidates, totalling 20 fits


/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:497: UserWarning: class_weight presets "balanced" or "balanced_subsample" are not recommended for warm_start if the fitted data differs from the full dataset. In order to use "balanced" weights, use compute_class_weight("balanced", classes, y). In place of y you can use a large enough sample of the full training set target to properly estimate the class frequency distributions. Pass the resulting weights as the class_weight parameter.
  warn('class_weight presets "balanced" or "balanced_subsample" are '
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:497: UserWarning: class_weight presets "balanced" or "balanced_subsample" are not recommended for warm_start if the fitted data differs from the full dataset. In order to use "balanced" weights, use compute_class_weight("balanced", classes, y). In place of y you can use a large enough sample of the full training set target to properly 

[Parallel(n_jobs=-1)]: Done 442 tasks      | elapsed:   27.2s
[Parallel(n_jobs=-1)]: Done 442 tasks      | elapsed:   28.2s
[Parallel(n_jobs=-1)]: Done 442 tasks      | elapsed:   28.2s
[Parallel(n_jobs=-1)]: Done 442 tasks      | elapsed:   27.8s
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:   31.1s finished
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    0.4s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    0.9s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    1.0s finished
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:   32.1s finished
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.2s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    0.4s
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:   30.7s finished
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:   31.3s finished
[Parallel(n_jobs=4)]: Done 442 t

[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.4s
[Parallel(n_jobs=-1)]: Done  42 tasks      | elapsed:    2.4s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    1.6s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    1.5s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    2.9s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    3.2s finished
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    3.5s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    4.0s finished
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:497: UserWarning: class_weight presets "balanced" or "balanced_subsample" are not recommended for warm_start if the fitted data differs from the full dataset. In order to use "balanced" weights, use compute_class_weight("balanced", classes, y). In place of y you can use a large enough sample of the full training set target to properly estimate the class frequency distributions. Pass the resulting weights as the c

[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    4.2s finished
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    0.5s
[Parallel(n_jobs=-1)]: Done 442 tasks      | elapsed:   31.7s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    1.0s
[Parallel(n_jobs=-1)]: Done 442 tasks      | elapsed:   30.5s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    1.1s finished
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.2s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    1.2s
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:   34.9s finished
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    2.8s
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:   33.8s finished
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    3.0s finished
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done 192 tasks

GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=None, shuffle=True),
       error_score='raise',
       estimator=RandomForestClassifier(bootstrap=True, class_weight='balanced',
            criterion='gini', max_depth=None, max_features='auto',
            max_leaf_nodes=None, min_impurity_decrease=0.0,
            min_impurity_split=None, min_samples_leaf=1,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            n_estimators=500, n_jobs=-1, oob_score=False,
            random_state=None, verbose=1, warm_start=True),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'max_depth': (7, 8), 'min_samples_leaf': (2, 5)},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=1)

In [32]:
gsRF.best_score_

0.7192700496451173

In [33]:
gsRF.best_params_

{'max_depth': 8, 'min_samples_leaf': 5}

In [61]:
best_RF = gsRF.best_estimator_
best_RF.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])

/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:497: UserWarning: class_weight presets "balanced" or "balanced_subsample" are not recommended for warm_start if the fitted data differs from the full dataset. In order to use "balanced" weights, use compute_class_weight("balanced", classes, y). In place of y you can use a large enough sample of the full training set target to properly estimate the class frequency distributions. Pass the resulting weights as the class_weight parameter.
  warn('class_weight presets "balanced" or "balanced_subsample" are '
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:305: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  warn("Warm-start fitting without increasing n_estimators does not "


RandomForestClassifier(bootstrap=True, class_weight='balanced',
            criterion='gini', max_depth=8, max_features='auto',
            max_leaf_nodes=None, min_impurity_decrease=0.0,
            min_impurity_split=None, min_samples_leaf=5,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            n_estimators=500, n_jobs=-1, oob_score=False,
            random_state=None, verbose=1, warm_start=True)

In [62]:
dropped_test['0'] = best_RF.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]
dropped_test['0'].to_csv('submissionRF.csv',header = True, index_label = True)
dropped_test.head()

[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.0s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    0.2s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    0.2s finished


0  1  2  3  4  6         7  8  10  12 ...        336  337  338  339  \
0  0.461148  1  0  0  1  0  0.136364  0   1   1 ...   0.192984    0    1    0   
1  0.649069  1  0  0  1  0  0.181818  0   1   1 ...   0.195690    0    1    0   
2  0.467764  1  0  0  0  0  0.090909  0   1   1 ...   0.192984    0    1    0   
3  0.610451  1  0  0  1  0  0.090909  0   1   1 ...   0.195690    0    1    0   
4  0.738272  1  0  0  1  0  0.090909  0   1   1 ...   0.289893    0    0    1   

   340       341  342  343  344  345  
0    0  0.222222    1    1    1    1  
1    0  0.000000    1    1    1    0  
2    0  0.222222    1    1    1    0  
3    0  0.000000    1    1    1    0  
4    0  0.000000    1    1    1    1  

[5 rows x 312 columns]

In [307]:
X_train, X_testV, y_train, y_testV = train_test_split(dropped_train.drop(['0'], axis = 1), dropped_train['0'],
                                                    test_size = 0.2,
                                                    random_state = 42, stratify = dropped_train['0'])
X_train.shape, X_testV.shape

((24301, 311), (6076, 311))

In [308]:
from scipy.stats import rankdata
best_RF.fit(X_train, y_train)
best_LogRegBagging.fit(X_train, y_train)
roc_auc_score(y_testV, 0.5*(best_RF.predict_proba(X_testV)[:, 1])
              + 0.5*(best_LogRegBagging.predict_proba(X_testV)[:, 1]))

/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:497: UserWarning: class_weight presets "balanced" or "balanced_subsample" are not recommended for warm_start if the fitted data differs from the full dataset. In order to use "balanced" weights, use compute_class_weight("balanced", classes, y). In place of y you can use a large enough sample of the full training set target to properly estimate the class frequency distributions. Pass the resulting weights as the class_weight parameter.
  warn('class_weight presets "balanced" or "balanced_subsample" are '
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:305: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  warn("Warm-start fitting without increasing n_estimators does not "
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/bagging.py:348: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  w

0.7773182988724155

In [309]:
roc_auc_score(y_testV, rankdata((best_RF.predict_proba(X_testV)[:, 1]))
              + rankdata((best_LogRegBagging.predict_proba(X_testV)[:, 1])))

[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.0s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    0.2s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    0.3s finished


0.7822885790508362

In [310]:
roc_auc_score(y_testV, 0.7*(best_RF.predict_proba(X_testV)[:, 1])
              + 0.3*(best_LogRegBagging.predict_proba(X_testV)[:, 1]))

[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.0s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    0.2s
[Parallel(n_jobs=4)]: Done 500 out of 500 | elapsed:    0.2s finished


0.7877366728430558

In [311]:
best_RF.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])
best_LogRegBagging.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])

dropped_test['0'] = (0.7*(best_RF.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1])
                            + 0.3*(best_LogRegBagging.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]))
dropped_test['0'].to_csv('submissionEns.csv',header = True, index_label = True)
dropped_test.head()

/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:497: UserWarning: class_weight presets "balanced" or "balanced_subsample" are not recommended for warm_start if the fitted data differs from the full dataset. In order to use "balanced" weights, use compute_class_weight("balanced", classes, y). In place of y you can use a large enough sample of the full training set target to properly estimate the class frequency distributions. Pass the resulting weights as the class_weight parameter.
  warn('class_weight presets "balanced" or "balanced_subsample" are '
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:305: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  warn("Warm-start fitting without increasing n_estimators does not "
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/bagging.py:348: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  w

0  1  2  3  4  6         7  8  10  12 ...        336  337  338  339  \
0  0.416062  1  0  0  1  0  0.136364  0   1   1 ...   0.192984    0    1    0   
1  0.689477  1  0  0  1  0  0.181818  0   1   1 ...   0.195690    0    1    0   
2  0.488287  1  0  0  0  0  0.090909  0   1   1 ...   0.192984    0    1    0   
3  0.637244  1  0  0  1  0  0.090909  0   1   1 ...   0.195690    0    1    0   
4  0.750120  1  0  0  1  0  0.090909  0   1   1 ...   0.289893    0    0    1   

   340       341  342  343  344  345  
0    0  0.222222    1    1    1    1  
1    0  0.000000    1    1    1    0  
2    0  0.222222    1    1    1    0  
3    0  0.000000    1    1    1    0  
4    0  0.000000    1    1    1    1  

[5 rows x 312 columns]

In [269]:
rf_predictions = []
lrb_predictions = []
ens_predictions = []

X = dropped_train.drop(['0'], axis = 1)
y = dropped_train['0']

for train, val in skf.split(X, y):
    best_RF.fit(X.iloc[train], y.iloc[train])
    best_LogRegBagging.fit(X.iloc[train], y.iloc[train])
    ens_predictions.append([y[val],  0.7*(best_RF.predict_proba(X.iloc[val])[:, 1])
              + 0.3*(best_LogRegBagging.predict_proba(X.iloc[val])[:, 1])])
    rf_predictions.append([y[val], best_RF.predict_proba(X.iloc[val])[:,1]])
    lrb_predictions.append([y[val], best_LogRegBagging.predict_proba(X.iloc[val])[:,1]])

/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:497: UserWarning: class_weight presets "balanced" or "balanced_subsample" are not recommended for warm_start if the fitted data differs from the full dataset. In order to use "balanced" weights, use compute_class_weight("balanced", classes, y). In place of y you can use a large enough sample of the full training set target to properly estimate the class frequency distributions. Pass the resulting weights as the class_weight parameter.
  warn('class_weight presets "balanced" or "balanced_subsample" are '
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:305: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  warn("Warm-start fitting without increasing n_estimators does not "
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/bagging.py:348: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  w

In [270]:
stacking_train = dropped_train.copy()

stacking_train["rf_preds"] = 0
stacking_train["lrb_preds"] = 0
stacking_train["ens_preds"] = 0

for i, fold in enumerate(skf.split(X, y)):
    train, val = fold[0], fold[1]
    stacking_train.iloc[val, -3] = rf_predictions[i][1]
    stacking_train.iloc[val, -2] = lrb_predictions[i][1]
    stacking_train.iloc[val, -1] = ens_predictions[i][1]

In [271]:
stacking_train

0  1  2  3  4  6         7  8  10  12    ...      339  340       341  \
0      1  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.222222   
1      1  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.111111   
2      0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.444444   
3      0  1  0  0  1  0  0.136364  0   1   1    ...        1    0  0.222222   
4      0  1  0  0  1  0  0.136364  0   1   1    ...        1    0  0.111111   
5      0  1  0  0  0  0  0.090909  0   0   1    ...        0    0  0.000000   
6      0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
7      0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.000000   
8      0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
9      0  1  0  0  0  0  0.136364  0   1   1    ...        0    0  0.000000   
10     0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
11     0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.222222   
12     0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
13     1  1  0  0  1  0  0.136364  0   1   1    ...        0    0  0.111111   
14     0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
15     0  1  0  0  1  0  0.090909  0   1   1    ...        1    0  0.000000   
16     0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.222222   
17     0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.222222   
18     1  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
19     0  1  0  0  0  0  0.136364  0   1   1    ...        0    0  0.000000   
20     1  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
21     1  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.000000   
22     0  1  0  0  0  0  0.136364  0   0   1    ...        0    0  0.444444   
23     0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.222222   
24     1  1  0  0  0  0  0.136364  0   1   1    ...        0    0  0.000000   
25     0  1  0  0  0  0  0.045455  0   1   1    ...        0    0  0.000000   
26     0  1  0  0  0  0  0.090909  0   0   1    ...        0    0  0.000000   
27     0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.000000   
28     0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
29     0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.000000   
...   .. .. .. .. .. ..       ... ..  ..  ..    ...      ...  ...       ...   
30469  0  1  0  0  0  0  0.090909  0   0   1    ...        0    0  0.000000   
30470  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30471  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30472  0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.444444   
30473  0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.222222   
30474  1  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.000000   
30475  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30476  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30477  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30478  0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.000000   
30479  1  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.111111   
30480  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30481  0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.000000   
30482  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30483  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30484  0  1  0  0  0  0  0.090909  0   1   1    ...        0    0  0.000000   
30485  0  1  0  0  1  0  0.090909  0   1   1    ...        0    0  0.444444   
30486  0  1  0  0  0  0  0.136364  0   1   1    ...        0    0  0.000000   
30487  0  1  0  0  1  0  0.090909  0   1   1    ...      

In [272]:
X_trainS, X_testSV, y_trainS, y_testSV = train_test_split(stacking_train.drop(['0'], axis = 1), stacking_train['0'],
                                                    test_size = 0.2,
                                                    random_state = 42, stratify = stacking_train['0'])
X_trainS.shape, X_testSV.shape

((24301, 314), (6076, 314))

In [273]:
from sklearn.ensemble import ExtraTreesClassifier
parameters = {'max_features': [5, 7, None], 'min_samples_leaf': [1, 3, 5], 'max_depth': [5,8,10]}
etc = ExtraTreesClassifier(n_estimators = 10, random_state = 42, n_jobs = -1)
etcv = GridSearchCV(etc, parameters, n_jobs=-1, cv=skf, verbose=1, scoring='roc_auc')
etcv.fit(stacking_train.drop(['0'], axis = 1), stacking_train['0'])

Fitting 5 folds for each of 27 candidates, totalling 135 fits


[Parallel(n_jobs=-1)]: Done  42 tasks      | elapsed:   19.1s
[Parallel(n_jobs=-1)]: Done 135 out of 135 | elapsed:  1.7min finished


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=None, shuffle=True),
       error_score='raise',
       estimator=ExtraTreesClassifier(bootstrap=False, class_weight=None, criterion='gini',
           max_depth=None, max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=-1,
           oob_score=False, random_state=42, verbose=0, warm_start=False),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'max_features': [5, 7, None], 'min_samples_leaf': [1, 3, 5], 'max_depth': [5, 8, 10]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=1)

In [274]:
etcv.best_params_

{'max_depth': 10, 'max_features': None, 'min_samples_leaf': 1}

In [312]:
bestET_stack = ExtraTreesClassifier(n_estimators = 1000, max_depth = 10, min_samples_leaf = 1, random_state = 42, n_jobs = -1)

In [313]:
best_LogRegBagging.fit(X_trainS, y_trainS)
bestET_stack.fit(X_trainS, y_trainS)

/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/bagging.py:348: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  warn("Warm-start fitting without increasing n_estimators does not "


ExtraTreesClassifier(bootstrap=False, class_weight=None, criterion='gini',
           max_depth=10, max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=1000, n_jobs=-1,
           oob_score=False, random_state=42, verbose=0, warm_start=False)

In [314]:
roc_auc_score(y_testSV, 0.35*(bestET_stack.predict_proba(X_testSV)[:, 1])
              + 0.65*(best_LogRegBagging.predict_proba(X_testSV)[:, 1]))

0.7508707597514257

In [315]:
best_RF.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])
best_LogRegBagging.fit(dropped_train.drop(['0'], axis = 1), dropped_train['0'])

stacking_test = dropped_test.copy()
rf_preds = best_RF.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]
lrb_preds = best_LogRegBagging.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]
ens_preds = (0.35*(best_RF.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1])
                            + 0.65*(best_LogRegBagging.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]))

stacking_test["rt_preds"] = 0
stacking_test["lrb_preds"] = 0
stacking_test["ens_preds"] = 0
stacking_test.iloc[:,-3] = best_RF.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]
stacking_test.iloc[:,-2] = best_LogRegBagging.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]
stacking_test.iloc[:,-1] = (0.7*(best_RF.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1])
                            + 0.3*(best_LogRegBagging.predict_proba(dropped_test.drop(['0'], axis = 1))[:, 1]))

stacking_test

/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:497: UserWarning: class_weight presets "balanced" or "balanced_subsample" are not recommended for warm_start if the fitted data differs from the full dataset. In order to use "balanced" weights, use compute_class_weight("balanced", classes, y). In place of y you can use a large enough sample of the full training set target to properly estimate the class frequency distributions. Pass the resulting weights as the class_weight parameter.
  warn('class_weight presets "balanced" or "balanced_subsample" are '
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/forest.py:305: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  warn("Warm-start fitting without increasing n_estimators does not "
/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/bagging.py:348: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  w

0  1  2  3  4  6         7  8  10  12    ...      339  340  \
0     0.416062  1  0  0  1  0  0.136364  0   1   1    ...        0    0   
1     0.689477  1  0  0  1  0  0.181818  0   1   1    ...        0    0   
2     0.488287  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
3     0.637244  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4     0.750120  1  0  0  1  0  0.090909  0   1   1    ...        1    0   
5     0.583022  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
6     0.292603  1  0  0  0  0  0.181818  0   1   1    ...        0    0   
7     0.450296  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
8     0.384761  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
9     0.569594  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
10    0.345060  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
11    0.796308  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
12    0.344889  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
13    0.464525  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
14    0.839969  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
15    0.491670  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
16    0.214408  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
17    0.538145  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
18    0.647504  1  0  0  1  0  0.136364  0   1   1    ...        0    0   
19    0.366458  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
20    0.375065  0  1  0  1  0  0.090909  0   1   1    ...        0    0   
21    0.581243  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
22    0.414977  1  0  0  0  0  0.136364  0   1   1    ...        0    0   
23    0.226757  1  0  0  0  0  0.090909  0   0   1    ...        0    0   
24    0.764605  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
25    0.630451  1  0  0  1  0  0.090909  0   1   1    ...        1    0   
26    0.761390  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
27    0.335396  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
28    0.318719  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
29    0.535364  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
...        ... .. .. .. .. ..       ... ..  ..  ..    ...      ...  ...   
4136  0.303133  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4137  0.253810  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4138  0.282723  1  0  0  0  0  0.045455  0   1   1    ...        0    0   
4139  0.430829  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4140  0.382703  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4141  0.538495  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4142  0.248297  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4143  0.366719  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4144  0.256033  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4145  0.380521  1  0  0  0  0  0.090909  0   0   1    ...        0    0   
4146  0.311667  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4147  0.402053  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4148  0.310071  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4149  0.519380  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4150  0.347507  1  0  0  0  0  0.090909  0   0   1    ...        0    0   
4151  0.366411  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4152  0.431536  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4153  0.656224  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4154  0.678872  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4155  0.509502  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4156  0.807282  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4157  0.459038  1  0  0  0  0  0.09090

In [317]:
best_LogRegBagging.fit(stacking_train.drop(['0'], axis = 1), stacking_train['0'])
bestET_stack.fit(stacking_train.drop(['0'], axis = 1), stacking_train['0'])

/home/anton/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/bagging.py:348: UserWarning: Warm-start fitting without increasing n_estimators does not fit new trees.
  warn("Warm-start fitting without increasing n_estimators does not "


ExtraTreesClassifier(bootstrap=False, class_weight=None, criterion='gini',
           max_depth=10, max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=1000, n_jobs=-1,
           oob_score=False, random_state=42, verbose=0, warm_start=False)

In [319]:
stacking_test['0'] = (0.35*(bestET_stack.predict_proba(stacking_test.drop(['0'], axis = 1))[:, 1])
              + 0.65*(best_LogRegBagging.predict_proba(stacking_test.drop(['0'], axis = 1))[:, 1]))
stacking_test['0'].to_csv('submissionStack.csv',header = True, index_label = True)
stacking_test

0  1  2  3  4  6         7  8  10  12    ...      339  340  \
0     0.268826  1  0  0  1  0  0.136364  0   1   1    ...        0    0   
1     0.609827  1  0  0  1  0  0.181818  0   1   1    ...        0    0   
2     0.425903  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
3     0.537393  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4     0.666270  1  0  0  1  0  0.090909  0   1   1    ...        1    0   
5     0.465977  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
6     0.209372  1  0  0  0  0  0.181818  0   1   1    ...        0    0   
7     0.352101  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
8     0.286682  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
9     0.480515  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
10    0.271988  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
11    0.711388  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
12    0.149501  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
13    0.383153  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
14    0.749503  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
15    0.367017  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
16    0.099959  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
17    0.461471  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
18    0.522529  1  0  0  1  0  0.136364  0   1   1    ...        0    0   
19    0.310204  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
20    0.201472  0  1  0  1  0  0.090909  0   1   1    ...        0    0   
21    0.480591  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
22    0.348908  1  0  0  0  0  0.136364  0   1   1    ...        0    0   
23    0.108440  1  0  0  0  0  0.090909  0   0   1    ...        0    0   
24    0.683949  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
25    0.590908  1  0  0  1  0  0.090909  0   1   1    ...        1    0   
26    0.629571  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
27    0.225694  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
28    0.198529  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
29    0.384005  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
...        ... .. .. .. .. ..       ... ..  ..  ..    ...      ...  ...   
4136  0.155980  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4137  0.156031  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4138  0.253235  1  0  0  0  0  0.045455  0   1   1    ...        0    0   
4139  0.335894  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4140  0.276343  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4141  0.478474  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4142  0.136501  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4143  0.288498  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4144  0.156935  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4145  0.268586  1  0  0  0  0  0.090909  0   0   1    ...        0    0   
4146  0.161727  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4147  0.276069  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4148  0.184162  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4149  0.417021  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4150  0.266564  1  0  0  0  0  0.090909  0   0   1    ...        0    0   
4151  0.247334  1  0  0  0  0  0.090909  0   1   1    ...        0    0   
4152  0.297830  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4153  0.598274  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4154  0.529807  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4155  0.344317  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4156  0.752514  1  0  0  1  0  0.090909  0   1   1    ...        0    0   
4157  0.412338  1  0  0  0  0  0.09090